# Amazon Review Analysis

Data source: https://nijianmo.github.io/amazon/index.html

Useful resources: 
- PySpark cheat sheet: http://web.utk.edu/~wfeng1/doc/cheatSheet_pyspark.pdf
- MLlib document: https://spark.apache.org/docs/latest/ml-guide.html
- SparkR document: https://spark.apache.org/docs/latest/sparkr.html
- SparkR tutorial: https://rpubs.com/wendyu/sparkr

## Before We Start...

Basic concepts of Spark: 
- RDD (Resilient Distributed Datasets): fundamental data structure for distributing data among cluster nodes. Immutable.
- Transformation: operations on RDD that returns an RDD, such as map, filter, reduce, and reduceByKey.
- Action: operations on RDD that returns a non-RDD value, such as collect.

We will be mainly using Spark Dataframe APIs instead of RDD APIs, to simplify development.
- Spark Dataframes are very similar to tables in relational databases. They have schema. Most of the operations on them are similar to querying a relational database as well. You can consider Spark Dataframe as a wrap on top of RDD.

## Loading Data

In [4]:
# Reading data from Delta Lake

amazon_review_raw = spark.sql("SELECT * FROM default.video_games_5")

In [5]:
display(amazon_review_raw)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label 0 5.0 0 true 10 17, 2015 A1HP7NVNPFMA4N 0700026657 Ambrosia075 This game is a bit hard to get the hang of, but when you do it's great. but when you do it's great. 1445040000 0 1 4.0 0 false 07 27, 2015 A1JGAP0185YJI6 0700026657 travis I played it a while but it was alright. The steam was a bit of trouble. The more they move these game to steam the more of a hard time I have activating and playing a game. But in spite of that it was fun, I liked it. Now I am looking forward to anno 2205 I really want to play my way to the moon. But in spite of that it was fun, I liked it 1437955200 0 2 3.0 0 true 02 23, 2015 A1YJWEXHQBWK2B 0700026657 Vincent G. Mezera ok game. Three Stars 1424649600 0 3 2.0 0 true 02 20, 2015 A2204E1TH211HT 0700026657 Grandma KR found the game a bit too complicated, not what I expected after having played 1602, 1503, and 1701 Two Stars 1424390400 0 4 5.0 0 true 12 25, 2014 A2RF5B5H74JLPE 0700026657 jon great game, I love it and have played it since its arrived love this game 1419465600 0 5 4.0 0 true 11 13, 2014 A11V6ZJ2FVQY1D 0700026657 IBRAHIM ALBADI i liked a lot some time that i haven't play a wonderfull game very simply and funny game verry good game. Anno 2070 1415836800 0 6 1.0 0 false 08 2, 2014 A1KXJ1ELZIU05C 0700026657 Creation27 I'm an avid gamer, but Anno 2070 is an INSULT to gaming. It is so buggy and half-finished that the first campaign doesn't even work properly and the DRM is INCREDIBLY frustrating to deal with. Once you manage to work your way past the massive amounts of bugs and get through the DRM, HOURS later you finally figure out that the game has no real tutorial, so you stuck just clicking around randomly. Sad, sad, sad, example of a game that could have been great but FTW. Avoid This Game - Filled with Bugs 1406937600 0 7 5.0 0 true 03 3, 2014 A1WK5I4874S3O2 0700026657 WhiteSkull I bought this game thinking it would be pretty cool and that i might play it for a week or two and be done. Boy was I wrong! From the moment I finally got the gamed Fired up (the other commentors on this are right, it takes forever and u are forced to create an account) I watched as it booted up I could tell right off the bat that ALOT of thought went into making this game. If you have ever played Sim city, then this game is a must try as you will easily navigate thru it and its multi layers. I have been playing htis now for a month straight, and I am STILL discovering layers of complexity in the game. There are a few things in the game that could used tweaked, but all in all this is a 5 star game. A very good game balance of skill with depth of choices 1393804800 0 8 5.0 0 true 02 21, 2014 AV969NA4CBP10 0700026657 Travis B. Moore I have played the old anno 1701 AND 1503. this game looks great but is more complex than the previous versions of the game. I found a lot of things lacking such as the sources of power and an inability to store energy with batteries or regenertive fuel cells as buildings in the game need power. Trade is about the same. My main beef with this it requires an internet connection. Other than that it has wonderful artistry and graphics. It is the same as anno 1701 but set in a future world where global warmming as flood the land and resource scarcity has sent human kind to look to the deep ocean for valuable minerals. I recoment the deep ocean expansion or complete if you get this. I found the ai instructor a little corny but other than that the game has some real polish. I wrote my 2 cents worth on suggestions on anno 2070 wiki and you can read 3 pages on that for game ideas I had. Anno 2070 more like anno 1701 1392940800 0 9 4.0 0 true 06 27, 2013 A1EO9BFUHTGWKZ 0700026657 johnnyz3 I liked it and had fun with it, played for a while and got my money's worth. You can certainly go further than I did but I got frustrated with the fact that here we are in this new start and still ta

## Cleaning Data

In [7]:
# Drop duplicates

print("Before duplication removal: ", amazon_review_raw.count())
amazon_review_distinct = amazon_review_raw.dropDuplicates(['reviewerID', 'asin'])
print("After duplication removal: ", amazon_review_distinct.count())

Before duplication removal: 487419
After duplication removal: 463283

In [8]:
# Convert Unix timestamp to readable date

from pyspark.sql.functions import from_unixtime, to_date

amazon_review_with_date = amazon_review_distinct.withColumn("reviewTime", to_date(from_unixtime(amazon_review_distinct.unixReviewTime))) \
                                                .drop("unixReviewTime")

# Fill in the empty vote column with 0, and convert it to numeric type

from pyspark.sql.types import *

amazon_review_fill_vote = amazon_review_with_date.withColumn("vote", amazon_review_with_date.vote.cast(IntegerType())) \
                                                 .fillna(0, subset=["vote"]) \

In [9]:
display(amazon_review_fill_vote)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary label 479357 1.0 0 true 2014-02-07 A0380485C177Q6QQNJIX B003N5ZYOG Franklin Tineo bad very bad the conect drums is broken bad very bad the conect drums is broken 0 78637 4.0 0 true 2015-01-10 A102MU6ZC9H1N6 B000EGELP0 Teresa Halbert My daughter still pulls this out from time to time just to see if she can still keep up with the puzzles. In great shape and purchase and price was good. Brain Age: Train Your Brain in Minutes a Day 0 186337 4.0 0 true 2013-03-26 A102MU6ZC9H1N6 B001TOQ8JS Teresa Halbert My son is Beatles crazy and when he saw this game, he was so excited to get it ordered and play it with his friends. The game was in good shape and the price was great. Xbox 360 The Beatles: rock Band 0 274182 5.0 0 true 2012-10-11 A1033LWHDCAJNQ B0083CJ2X8 S. Ali Limonadi Everything from all the previous Kingdom Hearts games, especially 1 & 2, has been leading up to this. I'm NOT going to spoil anything, but just in case you keep making excuses to not get this game: You find out who the man in the Brown Robe is. You find out every single thing about Organization 13. You find out what Riku is. (a blank blank). You find out who Xemnes is. (you only think you know, but this game will let you know the real deal) 2 of the worlds are waking worlds, not sleeping. And there's a 8th for pure cinematic. To unlock secret ending: Beginners mode is 10 to 13 tropies. Normal is 7 tropies......easy without even trying. Proud mode is just 3, I believe. I play with the 3D ON & all the way up 24/7 on every game, including, this......and I must say that games like this & Paper Mario & Kid Icarus & Luigi's Mansion were made for 3D. there was a few places were the frame rate dropped for 1 to 3 seconds, but if you did a Wireless Update and have either 4.2.0-9U or 4.4.0-10U then you won't have any problem.......and the latest Wireless Update Firmware is currently 4.4.0-10U. But the PS3 & 360 only do up to 24 fps with the 3D ON 24/7......so I have no complaints about the 3DS......especially now that I have Wireless Firmware Update 4.4.0-10U. The 3D Augmented Realty requires 0 cards, but you can use the cards to unlock rare Partners. Flowmotion is one of the easiest things to do in this game. You can Link & Dual Link with Spirits......I ended up just doing Dual Link for crazy new abilities during mostly Boss Battles. (because you have to build up your Link Gauge). There's also Reality Shift, which is more easier to do by just using your fingers on the Touch Screen, but sometimes I would used the Stylus after entering Reality Shift for certain things, like if it's a Sword for cutting the White Chains & Links on th touch screen. FYI According to the guy that makes every Kingdom Hearts game......"Reality Shift gives you a glimpse of a new gameplay that is exclusive to Kingdom Hearts 3 Only"..........at first this didn't make sense to me because each World has a completely different gameplay functionality for Reality Shift..........but then I thought about what they all have in common, which is Dual Screen interaction......so basically Kingdom Hearts 3 is either coming out on the Wii U or 3DS or both. Anyways everything has been leading up to Kingdom Hearts 3D, so I don't know what they are going to do in Kingdom Hearts 3, because everything has already been done in Kingdom Hearts 3D. But they do have a Tutorial for the previous 6 Kingdom Hearts games to read inside Kingdom Hearts 3D, so it's okay to start off with this......but I would still suggest playing Kingdom Hearts 1 & 2 as well as 3D.......and I hope 3 will be good. The Mark of Mastery comes with 5 3D AR Cards, like the Limited Edition $40 game at WalMart.......but you also get 12 artwork stuff & a great Kingdom Hearts 10th Anniversary 3DS case, which goes great with such 3DS colors as Red & Purple & maybe also White......but I have Blue and it doesn't look that good in bright areas, buti still love wearing it on 

As comparison, for pandas dataframe you will use .apply() to apply a function to a column. See: https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.apply.html

For example: amz_review['Date'] = amz_review['Time'].apply(to_date)

In [11]:
# Tokenization

from pyspark.ml.feature import RegexTokenizer

regexTokenizer = RegexTokenizer(inputCol="reviewText", outputCol="reviewWord", pattern="\\W")

amazon_review_tokenized = regexTokenizer.transform(amazon_review_fill_vote.fillna("", subset=["reviewText"]))

In [12]:
# Remove stop words

from pyspark.ml.feature import StopWordsRemover

remover = StopWordsRemover(inputCol="reviewWord", outputCol="reviewWordFiltered")
amazon_review_stop_word_removed = remover.transform(amazon_review_tokenized)

In [13]:
# Stemming

from nltk.stem.porter import PorterStemmer
from pyspark.sql.functions import udf

def stemming(col):
  p_stemmer = PorterStemmer()
  return [p_stemmer.stem(w) for w in col]

stemming_udf = udf(stemming, ArrayType(StringType()))
amazon_review_stemmed = amazon_review_stop_word_removed.withColumn("reviewWordCleaned", stemming_udf(amazon_review_stop_word_removed.reviewWordFiltered))

In [14]:
# Dropping temporary columns, and cache results (note that cache is also a lazy operation)

amazon_review_cleaned = amazon_review_stemmed.drop("reviewWord").drop("reviewWordFiltered").cache()

display(amazon_review_cleaned)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned 479357 1.0 0 true 2014-02-07 A0380485C177Q6QQNJIX B003N5ZYOG Franklin Tineo bad very bad the conect drums is broken bad very bad the conect drums is broken 0 List(bad, bad, conect, drum, broken) 78637 4.0 0 true 2015-01-10 A102MU6ZC9H1N6 B000EGELP0 Teresa Halbert My daughter still pulls this out from time to time just to see if she can still keep up with the puzzles. In great shape and purchase and price was good. Brain Age: Train Your Brain in Minutes a Day 0 List(daughter, still, pull, time, time, see, still, keep, puzzl, great, shape, purchas, price, good) 186337 4.0 0 true 2013-03-26 A102MU6ZC9H1N6 B001TOQ8JS Teresa Halbert My son is Beatles crazy and when he saw this game, he was so excited to get it ordered and play it with his friends. The game was in good shape and the price was great. Xbox 360 The Beatles: rock Band 0 List(son, beatl, crazi, saw, game, excit, get, order, play, friend, game, good, shape, price, great) 274182 5.0 0 true 2012-10-11 A1033LWHDCAJNQ B0083CJ2X8 S. Ali Limonadi Everything from all the previous Kingdom Hearts games, especially 1 & 2, has been leading up to this. I'm NOT going to spoil anything, but just in case you keep making excuses to not get this game: You find out who the man in the Brown Robe is. You find out every single thing about Organization 13. You find out what Riku is. (a blank blank). You find out who Xemnes is. (you only think you know, but this game will let you know the real deal) 2 of the worlds are waking worlds, not sleeping. And there's a 8th for pure cinematic. To unlock secret ending: Beginners mode is 10 to 13 tropies. Normal is 7 tropies......easy without even trying. Proud mode is just 3, I believe. I play with the 3D ON & all the way up 24/7 on every game, including, this......and I must say that games like this & Paper Mario & Kid Icarus & Luigi's Mansion were made for 3D. there was a few places were the frame rate dropped for 1 to 3 seconds, but if you did a Wireless Update and have either 4.2.0-9U or 4.4.0-10U then you won't have any problem.......and the latest Wireless Update Firmware is currently 4.4.0-10U. But the PS3 & 360 only do up to 24 fps with the 3D ON 24/7......so I have no complaints about the 3DS......especially now that I have Wireless Firmware Update 4.4.0-10U. The 3D Augmented Realty requires 0 cards, but you can use the cards to unlock rare Partners. Flowmotion is one of the easiest things to do in this game. You can Link & Dual Link with Spirits......I ended up just doing Dual Link for crazy new abilities during mostly Boss Battles. (because you have to build up your Link Gauge). There's also Reality Shift, which is more easier to do by just using your fingers on the Touch Screen, but sometimes I would used the Stylus after entering Reality Shift for certain things, like if it's a Sword for cutting the White Chains & Links on th touch screen. FYI According to the guy that makes every Kingdom Hearts game......"Reality Shift gives you a glimpse of a new gameplay that is exclusive to Kingdom Hearts 3 Only"..........at first this didn't make sense to me because each World has a completely different gameplay functionality for Reality Shift..........but then I thought about what they all have in common, which is Dual Screen interaction......so basically Kingdom Hearts 3 is either coming out on the Wii U or 3DS or both. Anyways everything has been leading up to Kingdom Hearts 3D, so I don't know what they are going to do in Kingdom Hearts 3, because everything has already been done in Kingdom Hearts 3D. But they do have a Tutorial for the previous 6 Kingdom Hearts games to read inside Kingdom Hearts 3D, so it's okay to start off with this......but I would still suggest playing Kingdom Hearts 1 & 2 as well as 3D.......and I hope 3 will be good. The Mark of Mastery comes with 5 3D AR Cards, like the Limited Edition $40 game at WalMart.......

## Exploratory Analysis

In [16]:
# Let's use Spark SQL for some simple exploratory analysis. Firstly, we need to create a temporary view based on the dataframe.

amazon_review_cleaned.createOrReplaceTempView("amazon_book_reviews")

In [17]:
# Distribution of the star ratings of book reviews

star_rating = spark.sql('''
  SELECT 
    overall AS star_rating, 
    COUNT(*) AS count 
  FROM
    amazon_book_reviews
  GROUP BY
    overall
  ORDER BY
    overall
''')

display(star_rating)

star_rating count 1.0 28449 2.0 22327 3.0 45614 4.0 86789 5.0 280104

In [18]:
# Number of reviews over time

review_over_time = spark.sql('''
  SELECT 
    reviewTime AS date, 
    COUNT(*) AS count 
  FROM
    amazon_book_reviews
  WHERE
    reviewTime >= '2015-01-01'
  GROUP BY
    reviewTime
  ORDER BY
    reviewTime
''')

display(review_over_time)

date count 2015-01-01 432 2015-01-02 382 2015-01-03 501 2015-01-04 389 2015-01-05 392 2015-01-06 375 2015-01-07 436 2015-01-08 303 2015-01-09 397 2015-01-10 248 2015-01-11 320 2015-01-12 378 2015-01-13 342 2015-01-14 378 2015-01-15 281 2015-01-16 265 2015-01-17 192 2015-01-18 295 2015-01-19 216 2015-01-20 302 2015-01-21 263 2015-01-22 314 2015-01-23 222 2015-01-24 224 2015-01-25 245 2015-01-26 262 2015-01-27 169 2015-01-28 261 2015-01-29 249 2015-01-30 213 2015-01-31 255 2015-02-01 244 2015-02-02 358 2015-02-03 226 2015-02-04 387 2015-02-05 208 2015-02-06 261 2015-02-07 178 2015-02-08 265 2015-02-09 289 2015-02-10 296 2015-02-11 434 2015-02-12 299 2015-02-13 271 2015-02-14 301 2015-02-15 264 2015-02-16 387 2015-02-17 427 2015-02-18 440 2015-02-19 412 2015-02-20 351 2015-02-21 305 2015-02-22 296 2015-02-23 447 2015-02-24 430 2015-02-25 266 2015-02-26 420 2015-02-27 326 2015-02-28 308 2015-03-01 395 2015-03-02 391 2015-03-03 421 2015-03-04 412 2015-03-05 257 2015-03-06 302 2015-03-07 230 2015-03-08 188 2015-03-09 366 2015-03-10 294 2015-03-11 290 2015-03-12 232 2015-03-13 202 2015-03-14 193 2015-03-15 183 2015-03-16 313 2015-03-17 309 2015-03-18 199 2015-03-19 212 2015-03-20 304 2015-03-21 271 2015-03-22 240 2015-03-23 230 2015-03-24 309 2015-03-25 261 2015-03-26 276 2015-03-27 204 2015-03-28 217 2015-03-29 269 2015-03-30 329 2015-03-31 228 2015-04-01 263 2015-04-02 282 2015-04-03 209 2015-04-04 277 2015-04-05 254 2015-04-06 288 2015-04-07 274 2015-04-08 241 2015-04-09 342 2015-04-10 232 2015-04-11 255 2015-04-12 142 2015-04-13 242 2015-04-14 242 2015-04-15 299 2015-04-16 262 2015-04-17 248 2015-04-18 183 2015-04-19 228 2015-04-20 272 2015-04-21 276 2015-04-22 221 2015-04-23 256 2015-04-24 161 2015-04-25 156 2015-04-26 197 2015-04-27 207 2015-04-28 195 2015-04-29 280 2015-04-30 213 2015-05-01 178 2015-05-02 174 2015-05-03 231 2015-05-04 230 2015-05-05 200 2015-05-06 192 2015-05-07 193 2015-05-08 234 2015-05-09 218 2015-05-10 169 2015-05-11 256 2015-05-12 226 2015-05-13 227 2015-05-14 226 2015-05-15 230 2015-05-16 127 2015-05-17 206 2015-05-18 239 2015-05-19 209 2015-05-20 199 2015-05-21 240 2015-05-22 172 2015-05-23 157 2015-05-24 195 2015-05-25 143 2015-05-26 220 2015-05-27 257 2015-05-28 171 2015-05-29 232 2015-05-30 196 2015-05-31 142 2015-06-01 193 2015-06-02 145 2015-06-03 305 2015-06-04 212 2015-06-05 218 2015-06-06 211 2015-06-07 141 2015-06-08 221 2015-06-09 242 2015-06-10 157 2015-06-11 245 2015-06-12 166 2015-06-13 141 2015-06-14 205 2015-06-15 201 2015-06-16 218 2015-06-17 185 2015-06-18 201 2015-06-19 199 2015-06-20 182 2015-06-21 190 2015-06-22 235 2015-06-23 338 2015-06-24 236 2015-06-25 190 2015-06-26 181 2015-06-27 176 2015-06-28 196 2015-06-29 215 2015-06-30 174 2015-07-01 195 2015-07-02 215 2015-07-03 172 2015-07-04 185 2015-07-05 163 2015-07-06 241 2015-07-07 209 2015-07-08 280 2015-07-09 269 2015-07-10 294 2015-07-11 199 2015-07-12 196 2015-07-13 210 2015-07-14 257 2015-07-15 234 2015-07-16 255 2015-07-17 170 2015-07-18 241 2015-07-19 171 2015-07-20 253 2015-07-21 230 2015-07-22 312 2015-07-23 198 2015-07-24 212 2015-07-25 208 2015-07-26 155 2015-07-27 202 2015-07-28 225 2015-07-29 213 2015-07-30 236 2015-07-31 220 2015-08-01 166 2015-08-02 203 2015-08-03 177 2015-08-04 275 2015-08-05 250 2015-08-06 221 2015-08-07 222 2015-08-08 142 2015-08-09 245 2015-08-10 312 2015-08-11 186 2015-08-12 237 2015-08-13 213 2015-08-14 192 2015-08-15 199 2015-08-16 151 2015-08-17 204 2015-08-18 199 2015-08-19 214 2015-08-20 218 2015-08-21 193 2015-08-22 204 2015-08-23 153 2015-08-24 214 2015-08-25 277 2015-08-26 305 2015-08-27 217 2015-08-28 210 2015-08-29 142 2015-08-30 159 2015-08-31 312 2015-09-01 207 2015-09-02 215 2015-09-03 228 2015-09-04 255 2015-09-05 228 2015-09-06 135 2015-09-07 169 2015-09-08 172 2015-09-09 180 2015-09-10 236 2015-09-11 217 2015-09-12 167 2015-09-13 155 2015-09-14 211 2015-09-15 218 2015-09-16 170 2015-09-17 223 2015-09-18 239 2015-09-19 173 2015-09-20 173 2015-09-21 188 2015-09-22 214 2015-09-23 296

## Review Score Prediction

As comparison, without Spark we commonly use sklearn in Python for machine learning (read more: https://scikit-learn.org/stable/user_guide.html); or NLTK for natural language processing (read more: https://www.nltk.org/)

In [21]:
# Extract verified 5-star and 1-star reviews for prediction

prediction_df = amazon_review_cleaned.where( ((amazon_review_cleaned.overall == 1) | (amazon_review_cleaned.overall == 5)) \
                                             & amazon_review_cleaned.verified == True )

# This is equivalent to the following Spark SQL command:

prediction_df = spark.sql("SELECT * FROM amazon_book_reviews WHERE (overall = 1 OR overall = 5) AND verified = TRUE")

display(prediction_df)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned 479357 1.0 0 true 2014-02-07 A0380485C177Q6QQNJIX B003N5ZYOG Franklin Tineo bad very bad the conect drums is broken bad very bad the conect drums is broken 0 List(bad, bad, conect, drum, broken) 274182 5.0 0 true 2012-10-11 A1033LWHDCAJNQ B0083CJ2X8 S. Ali Limonadi Everything from all the previous Kingdom Hearts games, especially 1 & 2, has been leading up to this. I'm NOT going to spoil anything, but just in case you keep making excuses to not get this game: You find out who the man in the Brown Robe is. You find out every single thing about Organization 13. You find out what Riku is. (a blank blank). You find out who Xemnes is. (you only think you know, but this game will let you know the real deal) 2 of the worlds are waking worlds, not sleeping. And there's a 8th for pure cinematic. To unlock secret ending: Beginners mode is 10 to 13 tropies. Normal is 7 tropies......easy without even trying. Proud mode is just 3, I believe. I play with the 3D ON & all the way up 24/7 on every game, including, this......and I must say that games like this & Paper Mario & Kid Icarus & Luigi's Mansion were made for 3D. there was a few places were the frame rate dropped for 1 to 3 seconds, but if you did a Wireless Update and have either 4.2.0-9U or 4.4.0-10U then you won't have any problem.......and the latest Wireless Update Firmware is currently 4.4.0-10U. But the PS3 & 360 only do up to 24 fps with the 3D ON 24/7......so I have no complaints about the 3DS......especially now that I have Wireless Firmware Update 4.4.0-10U. The 3D Augmented Realty requires 0 cards, but you can use the cards to unlock rare Partners. Flowmotion is one of the easiest things to do in this game. You can Link & Dual Link with Spirits......I ended up just doing Dual Link for crazy new abilities during mostly Boss Battles. (because you have to build up your Link Gauge). There's also Reality Shift, which is more easier to do by just using your fingers on the Touch Screen, but sometimes I would used the Stylus after entering Reality Shift for certain things, like if it's a Sword for cutting the White Chains & Links on th touch screen. FYI According to the guy that makes every Kingdom Hearts game......"Reality Shift gives you a glimpse of a new gameplay that is exclusive to Kingdom Hearts 3 Only"..........at first this didn't make sense to me because each World has a completely different gameplay functionality for Reality Shift..........but then I thought about what they all have in common, which is Dual Screen interaction......so basically Kingdom Hearts 3 is either coming out on the Wii U or 3DS or both. Anyways everything has been leading up to Kingdom Hearts 3D, so I don't know what they are going to do in Kingdom Hearts 3, because everything has already been done in Kingdom Hearts 3D. But they do have a Tutorial for the previous 6 Kingdom Hearts games to read inside Kingdom Hearts 3D, so it's okay to start off with this......but I would still suggest playing Kingdom Hearts 1 & 2 as well as 3D.......and I hope 3 will be good. The Mark of Mastery comes with 5 3D AR Cards, like the Limited Edition $40 game at WalMart.......but you also get 12 artwork stuff & a great Kingdom Hearts 10th Anniversary 3DS case, which goes great with such 3DS colors as Red & Purple & maybe also White......but I have Blue and it doesn't look that good in bright areas, buti still love wearing it on my 3DS 24/7 anyways. So besides Heartless & Nobodies, there is also just a walking Heart, as well as ISO's & Spirits & Nightmares & Dream Eaters & Reapers. Basically, they are clearly making a sequel for the World Ends With You, for the 3DS. Like Kingdom Hearts 1 & 2......3D is also a main game. Quite frankly, I now don't know how I will play this game without Flowmotion & Reality Shift & Dual Links in the upcoming Kingdom Hearts 3........so I guess you could say that this game has r

In [22]:
# Take a stratified sample

print("Number of rows before sampling: ", prediction_df.count())
prediction_df_sampled = prediction_df.sampleBy("overall", fractions = {1:0.001, 5:0.001}, seed = 16).cache()
print("Number of rows after sampling: ", prediction_df_sampled.count())

Number of rows before sampling: 221619
Number of rows after sampling: 259

### TF-IDF with Hashing Trick + Random Forest

In [24]:
# Copy prediction data

prediction_tfidf_hash = prediction_df_sampled.select('*')

In [25]:
# Extract bigram

from pyspark.ml.feature import NGram
from pyspark.sql.functions import array_union

ngram = NGram(n = 2, inputCol="reviewWordCleaned", outputCol="reviewBigrams")
prediction_tfidf_hash = ngram.transform(prediction_tfidf_hash)

prediction_tfidf_hash = prediction_tfidf_hash.withColumn("reviewNgrams", \
                                                         array_union(prediction_tfidf_hash.reviewWordCleaned, \
                                                                     prediction_tfidf_hash.reviewBigrams))

In [26]:
# Getting tf-idf values for 1-2grams

from pyspark.ml.feature import HashingTF, IDF

hashtf = HashingTF(numFeatures=2**12, inputCol="reviewNgrams", outputCol='TF')
tf = hashtf.transform(prediction_tfidf_hash)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf)
prediction_tfidf_hash = idfModel.transform(tf)

In [27]:
display(prediction_tfidf_hash)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned reviewBigrams reviewNgrams TF TF-IDF 321107 5.0 0 true 2014-07-04 ARW4UBHTV3OCS B00E4MQODC Anon It work as well as my G700, but with battery life that makes it actually practical to use as a wireless mouse. Great shape, textures, button layout, and tracking. The only things the G700 has on it are wheel functions: I miss the express scroll function a lot, and not having side scrolling on the wheel is slightly missed. Fantastic wireless gaming mouse. 0 List(work, well, g700, batteri, life, make, actual, practic, use, wireless, mous, great, shape, textur, button, layout, track, thing, g700, wheel, function, miss, express, scroll, function, lot, side, scroll, wheel, slightli, miss) List(work well, well g700, g700 batteri, batteri life, life make, make actual, actual practic, practic use, use wireless, wireless mous, mous great, great shape, shape textur, textur button, button layout, layout track, track thing, thing g700, g700 wheel, wheel function, function miss, miss express, express scroll, scroll function, function lot, lot side, side scroll, scroll wheel, wheel slightli, slightli miss) List(work, well, g700, batteri, life, make, actual, practic, use, wireless, mous, great, shape, textur, button, layout, track, thing, wheel, function, miss, express, scroll, lot, side, slightli, work well, well g700, g700 batteri, batteri life, life make, make actual, actual practic, practic use, use wireless, wireless mous, mous great, great shape, shape textur, textur button, button layout, layout track, track thing, thing g700, g700 wheel, wheel function, function miss, miss express, express scroll, scroll function, function lot, lot side, side scroll, scroll wheel, wheel slightli, slightli miss) List(0, 4096, List(60, 88, 116, 199, 393, 413, 421, 433, 485, 513, 762, 803, 881, 1152, 1175, 1182, 1227, 1259, 1287, 1288, 1333, 1344, 1382, 1457, 1491, 1575, 1645, 1654, 1657, 1844, 2064, 2098, 2100, 2114, 2192, 2269, 2325, 2341, 2448, 2605, 2631, 2811, 2899, 3359, 3437, 3454, 3489, 3633, 3701, 3809, 3822, 3894, 3929, 3935, 4068), List(1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(0, 4096, List(60, 88, 116, 199, 393, 413, 421, 433, 485, 513, 762, 803, 881, 1152, 1175, 1182, 1227, 1259, 1287, 1288, 1333, 1344, 1382, 1457, 1491, 1575, 1645, 1654, 1657, 1844, 2064, 2098, 2100, 2114, 2192, 2269, 2325, 2341, 2448, 2605, 2631, 2811, 2899, 3359, 3437, 3454, 3489, 3633, 3701, 3809, 3822, 3894, 3929, 3935, 4068), List(0.0, 2.7880929087757464, 0.0, 4.174387269895637, 3.7689221617874726, 1.9771626925594177, 3.9512437185814275, 2.670309873119363, 3.9512437185814275, 3.9512437185814275, 3.7689221617874726, 4.174387269895637, 3.481240089335692, 3.258096538021482, 3.3634570536793085, 3.9512437185814275, 0.0, 3.9512437185814275, 3.481240089335692, 3.481240089335692, 3.7689221617874726, 4.174387269895637, 3.6147714819602146, 0.0, 3.9512437185814275, 1.9497637183713032, 3.9512437185814275, 3.7689221617874726, 3.6147714819602146, 0.0, 3.7689221617874726, 3.6147714819602146, 4.174387269895637, 0.0, 3.6147714819602146, 0.0, 3.3634570536793085, 3.3634570536793085, 3.7689221617874726, 2.302585092994046, 3.258096538021482, 3.481240089335692, 2.7880929087757464, 3.6147714819602146, 0.0, 0.0, 3.7689221617874726, 3.3634570536793085, 2.2648447650111985, 0.0, 1.1539623837512747, 3.6147714819602146, 0.0, 2.3826278006675823, 3.258096538021482)) 434816 5.0 0 true 2017-01-29 A1G5EKIXBI6NRE B01CKH0W94 Mitch Product is high quality. Quick Effective Seller. Five Stars 0 List(product, high, qualiti, quick, effect, seller) List(product high, high qualiti, qualiti quick, quick effect, effect seller) List(product, high, qualiti, quick, effect, 

In [28]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(prediction_tfidf_hash)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_tfidf_hash.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)


In [29]:
display(predictions.select("overall", "indexedScore", "rawPrediction", "probability", "prediction", "predictedLabel"))

overall indexedScore rawPrediction probability prediction predictedLabel 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.24941095192512, 0.7505890480748778)) List(1, 2, List(), List(0.981235273798128, 0.018764726201871945)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(37.45762574668051, 2.5423742533194824)) List(1, 2, List(), List(0.936440643667013, 0.06355935633298707)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(36.50706720059278, 3.492932799407217)) List(1, 2, List(), List(0.9126766800148196, 0.08732331998518045)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(36.54999480646258, 3.450005193537425)) List(1, 2, List(), List(0.9137498701615645, 0.08625012983843564)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(37.739793835464155, 2.260206164535844)) List(1, 2, List(), List(0.9434948458866039, 0.05650515411339611)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(37.482604343205615, 2.51739565679438)) List(1, 2, List(), List(0.9370651085801406, 0.0629348914198595)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(34.529650853550905, 5.4703491464490925)) List(1, 2, List(), List(0.8632412713387726, 0.13675872866122732)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(37.51515967498086, 2.4848403250191398)) List(1, 2, List(), List(0.9378789918745214, 0.062121008125478494)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(38.46622996133283, 1.5337700386671709)) List(1, 2, List(), List(0.9616557490333207, 0.038344250966679275)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 1.0 1.0 List(1, 2, List(), List(37.52156634968461, 2.4784336503153845)) List(1, 2, List(), List(0.9380391587421153, 0.06196084125788461)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(38.459568277574306, 1.54043172242569)) List(1, 2, List(), List(0.9614892069393578, 0.03851079306064226)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(37.485022134236054, 2.5149778657639437)) List(1, 2, List(), List(0.9371255533559013, 0.0628744466440986)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.44638669435557, 0.5536133056444335)) List(1, 2, List(), List(0.9861596673588892, 0.013840332641110837)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(38.45160366391327, 1.548396336086729)) List(1, 2, List(), List(0.9612900915978317, 0.038709908402168224)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(33.52357848586104, 6.476421514138951)) List(1, 2, List(), List(0.8380894621465262, 0.16191053785347384)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(33.599027444565564, 6.400972555434431)) List(1, 2, List(), List(0.8399756861141393, 0.1600243138858608)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(39.427905575581036, 0.5720944244189637)) List(1, 2, List(), List(0.9856976393895259, 0.014302360610474093)) 0.0 5.0 5.0 0.0 List(1, 2, List(), List(32.09067118071621, 7.909328819283788)) List(1, 2, List(), List(0.8022667795179053, 

In [30]:
# Calculate AUC for train/test split

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.643836

In [31]:
# Performance evaluation with 5-fold cross validation

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=5)
cvModel = cv.fit(prediction_tfidf_hash)

print("Average AUC = %g" % cvModel.avgMetrics[0])

/databricks/spark/python/pyspark/ml/util.py:737: UserWarning: Cannot find mlflow module. To enable MLflow logging, install mlflow from PyPI.
 warnings.warn(_MLflowInstrumentation._NO_MLFLOW_WARNING)
Average AUC = 0.432662

### Doc2Vec + Random Forest

In [33]:
# Copy prediction data

prediction_doc2vec = prediction_df_sampled.select('*')

In [34]:
# Calculate Doc2Vec

from pyspark.ml.feature import Word2Vec

word2Vec = Word2Vec(inputCol="reviewWordCleaned", outputCol="doc2vec")
w2v_model = word2Vec.fit(prediction_doc2vec)

prediction_doc2vec = w2v_model.transform(prediction_doc2vec)

In [35]:
display(prediction_doc2vec)

reviewID overall vote verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned doc2vec 321107 5.0 0 true 2014-07-04 ARW4UBHTV3OCS B00E4MQODC Anon It work as well as my G700, but with battery life that makes it actually practical to use as a wireless mouse. Great shape, textures, button layout, and tracking. The only things the G700 has on it are wheel functions: I miss the express scroll function a lot, and not having side scrolling on the wheel is slightly missed. Fantastic wireless gaming mouse. 0 List(work, well, g700, batteri, life, make, actual, practic, use, wireless, mous, great, shape, textur, button, layout, track, thing, g700, wheel, function, miss, express, scroll, function, lot, side, scroll, wheel, slightli, miss) List(1, 100, List(), List(-0.001739057816467398, -0.001740884948371639, -0.005654011541346629, -0.006864674727342301, -0.004009725984125849, 0.005224136853470437, 0.003777420429903413, 0.003170951232013683, 9.680584508685335E-4, 0.004024521143536173, -1.3964162245693224E-4, 0.010217282778373167, 0.009680151458709471, 0.001778954335848891, -0.0037683945791345207, 0.0018595368657711774, 0.0024294513127496166, -0.008300936240102015, 0.004090982906129812, 0.009098673990416912, 0.004781835288139841, -0.003106387001612494, 0.0035216700090395826, -0.004005957357285004, 0.0035143427911304656, 2.89891310404205E-4, -0.001943070261228469, 3.837787033614492E-4, -0.00921634808483143, 5.013633072526464E-4, -0.0032372582673786147, -0.004009614176597566, -0.003787164324744334, -0.0026525449056568886, 0.003550103965080193, 0.003906347000250413, -9.005187443577714E-4, 0.0029247981447335933, -1.0330189440038896E-4, 5.01754502164981E-4, -2.4493291388235744E-4, -0.004859685792677825, -0.0028130240558135893, -0.0038717661518603563, 0.005446109616558157, 0.003282317364092676, 9.613934033099682E-7, 0.004292821874015874, -0.0077292130914546784, 0.005309816761573236, 0.0027207950911214275, -0.0039022449073531935, 7.779143822018898E-4, 0.005606214027671564, 4.53959428986925E-4, -0.004505529248666379, 0.0024494394648730032, -1.4639646941495517E-4, -0.0026106446297959455, 0.004049240100768304, -7.339779235002014E-4, 0.008837451076795977, 0.005435336351154312, -0.006997652284260238, -0.004751631006177875, 0.01045152389504496, 0.0017504526063754793, 0.0012733270451726932, 9.9251726867571E-4, -0.0028882236201165905, -0.0030789193246633776, 0.003906453614153208, 0.001289025501107737, 0.005596715633967711, 0.005501109626024, 0.001839894012758328, 0.00654343327116822, -0.004154805875112934, 3.832423789126258E-4, -0.0030534312301766005, 0.0040173482810778, -0.0040278767663685065, -0.005175469803713983, -0.005340438152122642, -0.0026855588019374876, 0.009362345065681203, 0.005898321257723916, 0.007879095662745738, 0.00273659429512918, -0.0022184345627113454, -0.005787386341140635, 0.0017511701782143884, 0.001617237360351869, 0.002411325447141163, 0.0033318605292738685, 0.005985518654568061, -0.004280053067862266, -0.008548047389805077, 0.004116966244539306, -0.004979017671317823)) 434816 5.0 0 true 2017-01-29 A1G5EKIXBI6NRE B01CKH0W94 Mitch Product is high quality. Quick Effective Seller. Five Stars 0 List(product, high, qualiti, quick, effect, seller) List(1, 100, List(), List(-0.003130931523628533, -8.651975804241374E-4, -0.004426174661299834, -0.0025741824841437238, -0.0014074601155395308, 0.0015870376373641193, 2.4803326232358813E-4, 0.003377680550329387, 4.0088181170479703E-4, 6.980187802885969E-4, 4.617229472690572E-4, 0.006896386155858636, 0.0028189145183811584, -2.7151093430196244E-4, -0.00468251493293792, 0.001488291968901952, 0.002140024919450904, -0.003662306582555175, 0.001063969025077919, 0.004734359215945005, 0.0021430464888301986, -7.095987384673208E-4, 0.0018709287396632135, -0.0011254975494618216, 0.0034865329701763885, -5.932013300480321E-5, 1.8221753028531867E-4, 5.96274194928507E-4, -0.00516478701805075, 5.004942261924346E-4, -0.003418778108122448, -6.219925126060843E-4, -0.002432872968

In [36]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(prediction_doc2vec)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="doc2vec", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_doc2vec.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.572139

In [37]:
# Performance evaluation with 10-fold cross validation

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=5)
cvModel = cv.fit(prediction_doc2vec)

print("Average AUC = %g" % cvModel.avgMetrics[0])

Average AUC = 0.385933

## Model Interpretation

In [39]:
# Extract bigram

interpret_tfidf = prediction_df_sampled.select('*')

from pyspark.ml.feature import NGram
from pyspark.sql.functions import array_union

ngram = NGram(n = 2, inputCol="reviewWordCleaned", outputCol="reviewBigrams")
interpret_tfidf = ngram.transform(interpret_tfidf)

interpret_tfidf = interpret_tfidf.withColumn("reviewNgrams", \
                                             array_union(interpret_tfidf.reviewWordCleaned, \
                                                         interpret_tfidf.reviewBigrams))

In [40]:
# Calculating TF-IDF without hashing; limit vocabulary to top 2^12 (4096) ngrams

from pyspark.ml.feature import CountVectorizer, IDF

tf = CountVectorizer(inputCol="reviewNgrams", outputCol='TF', minDF=2.0, vocabSize=2**12)
tf_model = tf.fit(interpret_tfidf)
tf_transformed = tf_model.transform(interpret_tfidf)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf_transformed)
interpret_tfidf = idfModel.transform(tf_transformed)

In [41]:
# Building a full Random Forest model with all the data, using TF-IDF embedding without hashing

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(interpret_tfidf)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

rf_model = pipeline.fit(interpret_tfidf)

In [42]:
# Getting feature importance from the Random Forest model

feature_importance = rf_model.stages[-2].featureImportances
print(feature_importance)

(1135,[0,1,2,4,6,7,8,9,12,13,14,17,18,21,22,23,24,26,27,28,29,30,31,35,37,39,40,42,43,46,48,52,53,54,55,56,59,60,61,63,64,69,70,71,72,75,77,80,82,83,84,86,87,88,89,90,94,98,100,101,103,104,105,106,114,124,127,131,140,141,143,144,145,147,148,149,151,157,158,160,165,166,168,170,178,181,182,188,191,194,197,205,206,211,212,214,224,225,229,231,232,234,237,245,247,256,262,269,271,276,277,280,282,285,286,287,304,307,308,311,312,313,316,317,321,322,328,329,333,337,345,346,347,350,352,357,365,366,371,372,374,382,386,392,395,398,410,421,426,434,440,441,442,446,450,451,463,464,470,477,478,479,485,486,492,495,498,501,506,509,515,520,522,524,535,537,540,541,547,552,554,564,577,586,588,589,595,598,602],[0.0060543021068574865,0.00865226097732997,0.00047470418037704604,0.020381643375317452,0.006906476779077168,0.001364278859494957,0.017430605739187255,0.0041507019322852,0.0072983135549441035,0.0041725185690317124,0.002879952565487154,0.0038357708945433978,0.008424297986181242,0.003962209533190616,0.004244289227186738,4.274402056934158e-05,0.004319561308904643,0.0025809979943113297,0.0014990008666335491,0.0002798432676781567,0.0022737980991582615,0.00046894992704028533,0.0024034613344653794,0.0007122529908405065,5.71025071522545e-06,0.0097440291622436,3.747830358791504e-05,0.0009232665775026699,0.001488666922781409,0.0008852541244656894,0.008811747807712947,0.000826880169488713,0.0021879970020089205,0.002584710659622728,0.00720237995468839,0.0045892688413339214,0.00642232964032238,0.015330110496875455,0.004983001747049044,0.0026344695217833643,0.011290196703618006,0.003096911390101888,0.005068399219002384,0.004355542651489718,0.0034047810596483158,0.005220981960180251,0.0022605451176610667,0.0022038738515023685,0.00012399441078350844,0.025997741735474884,0.005362694199749433,0.0023158952598961494,0.004234204791061411,0.0016668748623911323,0.00440774770300474,0.003305810777253556,0.0007003088862407459,0.0047783533002524565,0.0019839105725361207,0.004075274089468628,0.0005762473544509542,0.003096543323735752,0.0007439664647010416,0.001471180916297065,0.00663793361871067,0.0021812735265507805,0.005161648049099589,0.01949582048308449,0.005643469140138048,0.00010901009023084916,0.00290720589016321,0.002206771374445597,0.003001119702705133,0.02217113943219546,0.0010402226573280671,2.7962972851888045e-05,0.008451549135176647,0.002054043252364846,0.0006525096681611367,0.001884858504757906,0.0007603833127595828,0.005574955667712472,0.0021599644241153656,0.0033419633853075774,0.0006906893853777273,0.0036630153814654664,0.0005317035274354302,0.0012166133004153322,0.0019752145976290993,0.010481235877170765,0.0009874123081670245,0.0018672609976372369,0.0037306849391073155,0.004455951180410102,0.03895434824559621,0.001503699355009598,0.004105182361514794,0.0024059134710178675,0.0016821536380099494,0.008135841420060968,0.0031777507792016602,0.004645367085152836,0.0063816413554572265,0.010592677773538652,0.001983910572536121,0.007118203254164378,0.02514098051588231,0.004091259145167492,0.003400020236163787,0.0005956268897160693,0.015268797363563966,0.002236739972469097,0.002910461566922576,0.01075845363477533,0.004625873493377207,0.005996924042693493,0.0015207666255191653,0.004294407956554435,0.0025102769817624796,0.009142963613735925,0.0021828461751919317,0.00404649160568231,0.0013090787256693933,0.0021828461751919317,0.01004056546814852,0.0023753446690050954,0.004708941012358656,0.011271106404418016,0.0019530901632034297,0.0018227910361619001,0.0019141327800856426,0.002175440315340735,0.015157006419380174,0.007385763133354001,0.003993159860645361,0.005837379406375857,0.0077833416915354696,0.011105503982216946,0.003093525780895534,0.003144908260842183,0.0009347270966756759,0.004474360829224058,0.0010258031017902568,0.004399766296308152,0.0021312701034512734,0.0019839105725361207,0.0005131477951893488,0.004335511078529476,0.0008827085497782392,0.011801434634437113,0.002237037828150337,0.009239650708178502,0.00744624396963769,0.0013530311591012929,0.0015439095

In [43]:
# Get the top 20 most important feature's indices, and its importance metric

import numpy as np
import pandas as pd

top20_indice = np.flip(np.argsort(feature_importance.toArray()))[:20].tolist()
top20_importance = []
for index in top20_indice:
    top20_importance.append(feature_importance[index])

top20_df = spark.createDataFrame(pd.DataFrame(list(zip(top20_indice, top20_importance)), columns =['index', 'importance']))

display(top20_df)

index importance 212 0.03895434824559621 522 0.03220750876759737 588 0.03055272437272158 83 0.025997741735474884 262 0.02514098051588231 147 0.02217113943219546 4 0.020381643375317452 131 0.01949582048308449 463 0.018683124175626734 8 0.017430605739187255 589 0.016974194491952078 60 0.015330110496875455 277 0.015268797363563966 347 0.015157006419380174 479 0.014294300164200082 478 0.014044809157407198 501 0.012786422134204714 434 0.011801434634437113 64 0.011290196703618006 329 0.011271106404418016

In [44]:
# Create a map between each ngram and its index

from pyspark.sql.functions import explode, udf, col
from pyspark.sql.types import *

make_list_udf = udf(lambda col: [col], ArrayType(StringType()))
remove_list_udf = udf(lambda col: col[0], StringType())

def get_index(col):
  if len(col.indices) == 0:
    return -1   # Mark the ngram's index as -1 if it is not the top 2^12 ngrams
  else:
    return int(col.indices[0])
get_index_udf = udf(get_index, IntegerType())

ngram_index = interpret_tfidf.select(explode(interpret_tfidf.reviewNgrams).alias("reviewNgrams")).distinct() \
                             .withColumn("reviewNgrams", make_list_udf("reviewNgrams"))
ngram_index = tf_model.transform(ngram_index)
ngram_index = ngram_index.withColumn("reviewNgrams", remove_list_udf("reviewNgrams")) \
                         .withColumn("index", get_index_udf("TF")) \
                         .select("reviewNgrams", "index")

In [45]:
display(ngram_index.where(ngram_index.index > -1))

reviewNgrams index sit couch 651 still 27 hope 184 game like 222 imagin 401 art 427 time game 356 import 914 goe 1078 encount 663 keyboard 267 watch 837 without get 1033 know game 751 map 814 tri 47 ye 310 7 407 prevent 1079 stori 24 decis 1058 wall 358 ps3 180 follow instruct 941 quest 1101 day 94 excel game 907 logitech 859 fabul 1037 smoother 580 l 1067 even 28 good qualiti 676 battl 279 game anyway 812 got 37 dart 1105 ahead 1114 whether 482 like origin 445 game offer 817 recogn 446 rais 985 perman 832 two 104 extra 134 us 338 us game 1034 scale 860 game make 1120 realli 11 pirat 864 lack 761 present 547 true gamer 875 x 771 stock 1075 beaten 995 200 1116 ps 1025 act 441 boob 922 1 3 947 love thank 648 3d 272 burn 1133 progress 556 buy 26 upgrad 110 set 123 perfect 96 littl 62 somehow 421 length 789 ingeni 776 element 627 releas 200 greatest 384 piec 523 fact 461 game way 585 psp 406 multiplay 415 game d 439 name 488 mmo 713 gameplay 63 everyth els 858 upgrad choos 986 wouldn 741 strategi 305 seen 530 g 474 special 376 game love 877 fit like 538 ruin 579 storylin 1083 3 44 addit 232 put 50 mix 516 island 639 boy 958 probabl 168 stream 650 low 331 fp 359 80 90 902 certain 571 year old 354 show 249 pop 869 surviv 367 make sure 927 definit worth 447 kid love 400 bore 666 30 598 serious 515 confid 823 make game 308 shape 1113 insid 1128 sure 93 particular 497 touch 221 process 919 ship 130 option 228 month 387 lose 280 play control 794 daughter 408 hand 166 must 327 everi time 718 dlc 980 charg 83 seri 78 like game 644 game come 1134 game re 1096 rememb 879 non 321 new 23 re 29 stuff 442 noth 125 friend love 791 charact mani 619 green 1095 power 842 interact 816 perfectli 336 insan 1098 8 924 control move 1023 cant 391 work well 153 kinda 1070 xbox one 459 fun game 157 move around 582 also featur 1008 get consol 781 core 457 chang 154 own 335 good condit 731 thumb button 884 amazon 423 fulli 797 suck 212 girl 425 wasn 314 stick 262 back 35 sit 565 plu 170 man 298 lock 260 award 912 lol 297 exact 971 press 950 troubl 880 oem 901 fine 229 bundl 1074 add 196 visual 532 limit 734 headset want 753 differ feel 698 cast 608 remain 957 5 star 527 bro 642 boss 802 dual 472 deal 283 skin 841 stay 569 game ve 535 believ 479 lost 566 auto 987 softwar 322 face 955 ve never 843 slash 674 togeth 848 along 539 apart 1035 biggest 899 level 163 favor 564 stand 395 origin one 1028 get game 393 wide 709 lil 824 saw 261 rather 306 bring 596 main 567 m 25 friend 88 m sure 989 wow 784 juego 942 pokemon 799 experi 99 certainli 602 put game 658 develop 720 system 289 previou game 491 love 3 action 251 recommend peopl 662 difficult 966 spent 1052 game look 855 simpli amaz 1059 restart 929 top 590 soon 1024 batman 772 look great 555 achiev 332 coupl 288 safe 834 money 147 sticker 1073 recent 339 ambient 613 invest 1092 worth 56 great qualiti 835 one 6 els 243 great actual 758 kind 227 fix 1041 headset 350 sick 752 pleas 560 eventu 1097 buy game 1011 game lot 469 bit 95 featur 198 annoy 307 like wii 969 differ 73 smaller 1108 girl look 732 5 111 person 269 immedi 503 good product 462 major 940 display 550 normal 464 choos 804 make want 1094 area 1069 read 194 object 369 told 981 tell 710 tv 505 essenti 675 immers 994 think like 882 say 52 fli 821 grandson 935 direct 783 remot 468 entri 962 manag 522 peopl 45 wii u 546 larg hand 620 rate 383 lag 1062 ergonom 607 sound qualiti 490 excel 41 attack 792 take 167 content 259 mine 256 abl get 737 frustrat 739 gen 568 best game 183 tape 961 larg 211 came one 956 cabl 148 solid 494 nobodi 977 continu 433 treat 1057 blow 964 game much 1112 load 615 provid 563 challeng 253 super 146 cord 540 heavi 484 btw 870 great stori 1016 great 1 product work 475 ds 595 light 888 save money 881 detail 549 surpris 876 sneak 748 one greatest 670 gather 975 play like 348 onlin 217 avail 487 left 1104 fast 82 stori one 904 zero 631 practic 944 giant 913 1st 553 instead 352 kept 727 wire 250 head 699 ea 542 enough good 1129 answer 7

In [46]:
# Find the ngrams that map to the top 20 most important features

# Note that if you used hashingTF for word embedding, there would be multiple ngrams under the same index, because of the collision introduced by hashing, all of which would share and contribute to one importance score, and we don't have a way to separate their contribution to the importance score.
# Here in order to avoid such collision (so just one index per ngram), I used CountVectorizer instead of HashingTF during encoding.

import pyspark.sql.functions as f

top20_ngram = top20_df.join(ngram_index, on="index", how="left_outer")
display(top20_ngram.groupby("importance").agg(f.collect_list(top20_ngram.reviewNgrams).alias("reviewNgrams")).orderBy("importance", ascending=False))

importance reviewNgrams 0.03895434824559621 List(suck) 0.03220750876759737 List(manag) 0.03055272437272158 List(sometim) 0.025997741735474884 List(charg) 0.02514098051588231 List(stick) 0.02217113943219546 List(money) 0.020381643375317452 List(like) 0.01949582048308449 List(didn) 0.018683124175626734 List(classic) 0.017430605739187255 List(use) 0.016974194491952078 List(sell) 0.015330110496875455 List(nice) 0.015268797363563966 List(mayb) 0.015157006419380174 List(style) 0.014294300164200082 List(believ) 0.014044809157407198 List(hard get) 0.012786422134204714 List(game realli) 0.011801434634437113 List(nintendo ds) 0.011290196703618006 List(need) 0.011271106404418016 List(famili)